# __텍스트로 비디오 검색하기__

- 튜토리얼 난이도: ★★☆☆☆
- 읽는데 걸리는 시간: 7분
- 사용 언어: [SQL](https://ko.wikipedia.org/wiki/SQL) (100%)
- 실행 파일 위치: tutorial/thanosql_search/search_video_by_text.ipynb
- 참고 문서: [Kinetics-700](https://paperswithcode.com/dataset/kinetics-700), [X-CLIP](https://arxiv.org/abs/2207.07285)

## 튜토리얼 소개

<div class="admonition note">
    <h4 class="admonition-title">Multi-modal(멀티모달) 학습 이해하기</h4>
    <p>Multi-modal(멀티모달) 이란, 여러가지 형태의 정보를 통해 소통하는 환경을 의미하며, 여기서 modal(modality)는 데이터의 종류를 의미합니다.
        Multi-modal 데이터를 활용하여 진행하는 학습의 경우, 이미지 데이터, 텍스트 데이터, 센서 데이터 등 다양한 형태로 이루어진 데이터 특징을 효과적으로 학습하기에 하나의 현상에 대한 통합적인 분석을 가능하게 합니다. OpenAI의 CLIP이 대표적인 이미지-텍스트 멀티모달 딥러닝 모델로, 텍스트와 이미지를 함께 이해하는 데에 특화되어 있습니다.</p>
</div>

__아래는 ThanoSQL 텍스트-동영상 검색 알고리즘의 활용 및 예시 입니다.__

- 사용자가 보유하고 있는 동영상에서 원하는 장면을 텍스트로 묘사하고 이와 가장 유사한 동영상을 검색합니다.
- 유튜브 영상 등에서 내가 원하는 장면을 텍스트로 검색합니다.

<div class="admonition note">
    <h4 class="admonition-title">본 튜토리얼에서는</h4>
    <p>👉 이번 튜토리얼에서는 kinetics700-2020 데이터 세트를 사용합니다. kinetics는 DeepMind에서 공개한, 사람의 행동을 담고있는 영상들로 이루어진 대규모 데이터 세트입니다. kinetics700-2020은 2020년에 공개된 kinetics 데이터 세트의 새 버전으로, 700가지의 클래스에 대한 영상이 포함되어 있습니다.</p>
</div>

ThanoSQL의 X-CLIP 모델은 기존 이미지-텍스트 멀티모달인 CLIP모델을 확장하여 비디오와 텍스트의 관계를 이해할 수 있도록 학습된 모델입니다. 이번 튜토리얼에서는 텍스트를 입력하고 ThanoSQL 워크스페이스 데이터베이스 내에서 입력 텍스트와 유사한 비디오를 검색해주는 모델을 사용해보겠습니다.

## __0. 데이터 세트 및 모델 준비__

ThanoSQL의 쿼리 구문을 사용하기 위해서는 [ThanoSQL 워크스페이스](https://docs.thanosql.ai/1.4/ko/getting_started/paas/workspace/lab/)에서 언급된 것처럼 API 토큰을 생성하고 아래의 쿼리를 실행해야 합니다.

In [ ]:
%load_ext thanosql
%thanosql API_TOKEN=<발급받은_API_TOKEN>

### __데이터 세트 준비__

In [2]:
%%thanosql
GET THANOSQL DATASET kinetics700_data
OPTIONS (overwrite=True)

Success


<div class="admonition note">
    <h4 class="admonition-title">쿼리 세부 정보</h4>
    <ul>
        <li>"<strong>GET THANOSQL DATASET</strong>" 쿼리 구문을 사용하여 원하는 데이터 세트를 워크스페이스에 저장합니다.</li>
        <li>"<strong>OPTIONS</strong>" 쿼리 구문을 통해 <strong>GET THANOSQL DATASET</strong>에 사용할 옵션을 지정합니다.
        <ul>
            <li>"overwrite": 동일 이름의 데이터 세트가 존재하는 경우 덮어쓰기 가능 여부 설정. True일 경우 기존 데이터 세트는 새로운 데이터 세트로 변경됨 (bool, optional, True|False, default: False)</li>
        </ul>
        </li>
    </ul>
</div>

In [3]:
%%thanosql
COPY kinetics700
OPTIONS (if_exists='replace')
FROM 'thanosql-dataset/kinetics700_data/kinetics700.csv'

Success


<div class="admonition note">
    <h4 class="admonition-title">쿼리 세부 정보</h4>
    <ul>
        <li>"<strong>COPY</strong>" 쿼리 구문을 사용하여 데이터베이스에 저장 할 테이블명을 지정합니다.</li>
        <li>"<strong>OPTIONS</strong>" 쿼리 구문을 통해 <strong>COPY</strong>에 사용할 옵션을 지정합니다.
        <ul>
            <li>"if_exists": 동일 이름의 테이블이 존재하는 경우 처리하는 방법 설정. 오류 발생, 기존 테이블에 추가, 기존 테이블 대체 (str, optional, 'fail'|'replace'|'append', default: 'fail')</li>
        </ul>
        </li>
    </ul>
</div>

### __모델 준비__

In [4]:
%%thanosql
GET THANOSQL MODEL xclip
OPTIONS (
    model_name='tutorial_search_xclip',
    overwrite=True
    )

Success


<div class="admonition note">
    <h4 class="admonition-title">쿼리 세부 정보</h4>
    <ul>
        <li>"<strong>GET THANOSQL MODEL</strong>" 쿼리 구문을 사용하여 원하는 모델을 워크스페이스 및 데이터베이스에 저장합니다.</li>
        <li>"<strong>OPTIONS</strong>" 쿼리 구문을 통해 <strong>GET THANOSQL MODEL</strong>에 사용할 옵션을 지정합니다.
        <ul>
            <li>“model_name”: 저장할 모델의 이름 (str, optional)</li>
            <li>"overwrite": 동일 이름의 모델이 존재하는 경우 덮어쓰기 가능 여부 설정. True일 경우 기존 모델은 새로운 모델로 변경됨 (bool, optional, True|False, default: False)</li>
        </ul>
        </li>
    </ul>
</div>

## __1. 데이터 세트 확인__

본 튜토리얼을 진행하기 위해 ThanoSQL 워크스페이스 데이터베이스에 저장되어 있는 __kinetics700__ 테이블을 사용합니다. 아래의 쿼리 구문을 실행하고 테이블의 내용을 확인합니다.

In [5]:
%%thanosql
SELECT *
FROM kinetics700
LIMIT 5

video_path  \
0  thanosql-dataset/kinetics700_data/video/-dhP2A...   
1  thanosql-dataset/kinetics700_data/video/1ejgHK...   
2  thanosql-dataset/kinetics700_data/video/2Yvab3...   
3  thanosql-dataset/kinetics700_data/video/3nFLLc...   
4  thanosql-dataset/kinetics700_data/video/5PfhCJ...   

                      label  duration  
0            checking tires        10  
1                testifying        10  
2            checking tires        10  
3  punching person (boxing)        10  
4               kitesurfing        10

<div class="admonition note">
    <h4 class="admonition-title">데이터 테이블 이해하기</h4>
    <p><strong>kinetics700</strong> 테이블은 아래와 같은 정보를 담고 있습니다.</p>
    <ul>
        <li>video_path: 비디오 경로</li>
        <li>label: 비디오 라벨</li>
        <li>duration: 비디오 시간</li>
    </ul>
</div>

In [6]:
%%thanosql
PRINT VIDEO
AS
SELECT video_path
FROM kinetics700
LIMIT 2

/home/jovyan/thanosql-dataset/kinetics700_data/video/-dhP2AH0eqI.mp4


/home/jovyan/thanosql-dataset/kinetics700_data/video/1ejgHKw8E3Y.mp4


## __2.사전 학습된 모델을 사용하여 비디오 수치화__ 

다음 "__CONVERT USING__" 쿼리 구문을 실행하여 __kinetics700__ 비디오들을 수치화 합니다. 수치화 된 결과는 __kinetics700__ 테이블에 사용자가 옵션으로 지정한 이름(default: 'convert_result')의 컬럼에 저장됩니다.

In [7]:
%%thanosql
CONVERT USING tutorial_search_xclip
OPTIONS (
    video_col='video_path',
    result_col='convert_result'
    )
AS
SELECT *
FROM kinetics700

video_path  \
0   thanosql-dataset/kinetics700_data/video/-dhP2A...   
1   thanosql-dataset/kinetics700_data/video/1ejgHK...   
2   thanosql-dataset/kinetics700_data/video/2Yvab3...   
3   thanosql-dataset/kinetics700_data/video/3nFLLc...   
4   thanosql-dataset/kinetics700_data/video/5PfhCJ...   
..                                                ...   
93  thanosql-dataset/kinetics700_data/video/wwgl_8...   
94  thanosql-dataset/kinetics700_data/video/xICkLB...   
95  thanosql-dataset/kinetics700_data/video/xlRC0n...   
96  thanosql-dataset/kinetics700_data/video/yyy2Vy...   
97  thanosql-dataset/kinetics700_data/video/zb9HGN...   

                       label  duration  \
0             checking tires        10   
1                 testifying        10   
2             checking tires        10   
3   punching person (boxing)        10   
4                kitesurfing        10   
..                       ...       ...   
93              land sailing        10   
94             cutting nails        10   
95                testifying        10   
96            bench pressing        10   
97      country line dancing        10   

                                       convert_result  
0   [b'\x16', b'm', b'\xfb', b'\xbe', b'\xba', b'!...  
1   [b'X', b'\x05', b'\xe7', b'\xbe', b'\xf1', b'\...  
2   [b'\x10', b'\x96', b'\xfa', b'\xbe', b'\xff', ...  
3   [b'\x19', b'O', b' ', b'?', b'\xf8', b'\xbf', ...  
4   [b' ', b'u', b'\xa3', b'?', b'\x12', b'D', b'L...  
..                                                ...  
93  [b'\xb6', b'7', b'\xa0', b'?', b'\x9e', b']', ...  
94  [b'\xcd', b'\xe3', b'\x04', b'\xbf', b'\x94', ...  
95  [b'\x86', b'\xbb', b'_', b'\xbd', b'\x97', b'\...  
96  [b'B', b'\xd0', b'%', b'?', b'\xae', b'=', b'\...  
97  [b'>', b'\x1b', b'u', b'?', b'\xbe', b't', b'\...  

[98 rows x 4 columns]

<div class="admonition note">
    <h4 class="admonition-title">쿼리 세부 정보</h4>
    <ul>
        <li>"<strong>CONVERT USING</strong>" 쿼리 구문은 <strong>tutorial_search_xclip</strong> 모델을 비디오 수치화를 위한 알고리즘으로 사용합니다.</li>
        <li>"<strong>OPTIONS</strong>" 쿼리 구문을 통해 비디오 수치화 시 필요한 변수들을 정의합니다.
        <ul>
            <li>"video_col": 데이터 테이블에서 비디오의 경로를 담은 컬럼 (str, default: 'video_path')</li>
            <li>"result_col": 데이터 테이블에서 수치화된 결과를 담을 컬럼 이름 (str, optional, default: 'convert_result')</li>
        </ul>
        </li>
    </ul>
</div>

다음 "__CONVERT USING__" 쿼리 구문을 실행하여 변환된 결과를 다른 __ThanoSQL__ 쿼리 구문들과 함께 활용할 수 있도록 새로운 테이블에 저장해봅시다.

In [8]:
%%thanosql
CREATE TABLE kinetics700_convert AS 
SELECT * FROM ( 
    CONVERT USING tutorial_search_xclip
    OPTIONS (
        video_col='video_path',
        result_col='convert_result'
        )
    AS
    SELECT *
    FROM kinetics700
)

Success


## __3. 텍스트로 비디오 검색__

"__SEARCH VIDEO__" 쿼리 구문과 __tutorial_search_xclip__ 모델을 사용하여 텍스트 기반 비디오 검색을 할 수 있습니다. 다음 쿼리 구문을 실행하여 'bench press' 이라는 텍스트와 임베딩 된 __kinetics700__ 비디오들의 유사도를 계산합니다.

In [9]:
%%thanosql
SELECT video_path, label, score
FROM (
    SEARCH VIDEO
    USING tutorial_search_xclip
    OPTIONS (
        search_by='text',
        search_input='bench press',
        emb_col='convert_result',
        result_col='score',
        top_k=10
        )
    AS
    SELECT *
    FROM kinetics700_convert
    )

video_path  \
0  thanosql-dataset/kinetics700_data/video/qNB9qv...   
1  thanosql-dataset/kinetics700_data/video/yyy2Vy...   
2  thanosql-dataset/kinetics700_data/video/a9S4Ox...   
3  thanosql-dataset/kinetics700_data/video/ML7Oll...   
4  thanosql-dataset/kinetics700_data/video/zb9HGN...   
5  thanosql-dataset/kinetics700_data/video/AfKqHI...   
6  thanosql-dataset/kinetics700_data/video/6MWLkJ...   
7  thanosql-dataset/kinetics700_data/video/BEnKTN...   
8  thanosql-dataset/kinetics700_data/video/aKcKTY...   
9  thanosql-dataset/kinetics700_data/video/8DIU9c...   

                           label     score  
0                 bench pressing  0.312154  
1                 bench pressing  0.274932  
2                  golf chipping  0.202286  
3                     snowkiting  0.198646  
4           country line dancing  0.196104  
5                    parasailing  0.193912  
6                    kitesurfing  0.192512  
7                     snowkiting  0.190333  
8      opening bottle (not wine)  0.187058  
9  playing squash or racquetball  0.186208

<div class="admonition note">
    <h4 class="admonition-title">쿼리 세부 정보</h4>
    <ul>
        <li>"<strong>SEARCH VIDEO [image|text|audio|video]</strong>" 쿼리 구문은 검색하고자 하는 이미지|텍스트|오디오|비디오 파일을 정의합니다.</li>
        <li>"<strong>USING</strong>"은 비디오 수치화에 사용할 모델을 정의합니다.</li>
        <li>"<strong>OPTIONS</strong>" 쿼리 구문을 통해 비디오 검색 시 필요한 변수들을 정의합니다.
        <ul>
            <li>"search_by": 검색할 때 사용할 이미지|텍스트|오디오|비디오 타입 (str)</li>
            <li>"search_input": 검색할 때 사용할 입력값 (str)</li>
            <li>"emb_col": 데이터 테이블에서 수치화된 결과를 담은 컬럼 (str)</li>
            <li>"result_col": 데이터 테이블에서 검색 결과를 담을 컬럼 이름 (str, optional, default: 'search_result')</li>
            <li>"top_k": 반환할 행의 수. None을 입력할 시 데이터 테이블 전체를 반환 (int, optional, default: 1000)</li>
        </ul>
        </li>
        <li>"<strong>AS</strong>" 쿼리 구문은 검색에 사용할 임베딩 테이블을 정의합니다. <strong>kinetics700</strong> 테이블을 사용합니다.</li>
    </ul>
</div>

In [10]:
%%thanosql
PRINT VIDEO
AS (
    SELECT video_path
    FROM (
        SEARCH VIDEO
        USING tutorial_search_xclip
        OPTIONS (
            search_by='text',
            search_input='bench press',
            emb_col='convert_result',
            result_col='score',
            top_k=2
            )
        AS
        SELECT *
        FROM kinetics700_convert
        )
    )

/home/jovyan/thanosql-dataset/kinetics700_data/video/qNB9qv6PqwI.mp4


/home/jovyan/thanosql-dataset/kinetics700_data/video/yyy2Vy_5DjI.mp4


## __4. 튜토리얼을 마치며__

이번 튜토리얼에서는 kinetics700 데이터 세트를 사용하여 멀티 모달 텍스트/비디오 수치화와 수치화 결과를 바탕으로한 텍스트를 통한 비디오 검색까지 진행해 보았습니다. 초급 단계의 튜토리얼인 만큼 간단한 쿼리를 통해 눈에 보이는 결과를 얻는 것 위주로 진행했습니다. 비디오 검색을 조금 더 다채로운 쿼리와 함께 사용한다면, 보다 원하는 결과에 가까운 값을 얻을 수 있을 것입니다.

* [나만의 데이터 업로드하기](https://docs.thanosql.ai/1.4/ko/getting_started/data_upload/)
* [나만의 데이터 테이블 생성하기](https://docs.thanosql.ai/1.4/ko/how-to_guides/ThanoSQL_query/COPY_SYNTAX/)
* [나만의 모델 업로드하기](https://docs.thanosql.ai/1.4/ko/how-to_guides/ThanoSQL_query/UPLOAD_MODEL_SYNTAX/)

<div class="admonition tip">
    <h4 class="admonition-title">나만의 서비스를 위한 모델 배포 관련 문의</h4>
    <p>ThanoSQL을 활용해 나만의 모델을 만들거나, 나의 서비스에 적용하는데 어려움이 있다면 언제든 아래로 문의주세요😊</p>
    <p>텍스트-비디오 검색 모델 구축 관련 문의: <a href="mailto:contact@smartmind.team">contact@smartmind.team</a></p>
</div>